# Environment

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import matplotlib.pyplot as plt
%matplotlib inline

import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.offline import init_notebook_mode, iplot
from plotly.graph_objs import *
from plotly.subplots import make_subplots
import plotly.figure_factory as ff

In [3]:
# Basic
import os
import gc
import re
import sys
import glob
import numpy as np
import pandas as pd
from pathlib import Path
from pprint import pprint
import datetime

from collections import defaultdict
from typing import (List, Dict, Any, NoReturn, 
                    Tuple, Optional, Union)

from tqdm import tqdm, tqdm_notebook
import warnings
warnings.filterwarnings('ignore')

In [5]:
sys.path.insert(0,"..")

from config import init_config, config
from helpers import read_json, write_json, update_parameters
from eyemovements.filtering import sgolay_filter_dataset
from eyemovements.eyemovements_utils import (GazeState, get_movement_indexes)
from eyemovements.eyemovements_classifier import IVDT
from eyemovements.classification import classify_eyemovements_wrapper, run_eyemovements_classification
from eyemovements.eyemovements_metrics import estimate_quality, visualize_and_save
from create_training_dataset import TrainDataset

In [6]:
# System adjustments - for all colums to fit into output (default width is 80)
pd.options.display.width = 2500
pd.options.display.max_rows = 999
pd.set_option('display.max_rows', 1000)
pd.set_option('display.max_columns', None)
pd.options.display.max_colwidth = 100
sns.set_style("whitegrid")

## Define paths

In [7]:
CONFIG_FILE = "../set_locations.ini"
init_config(CONFIG_FILE)
TRAIN_DIR = config.get("DataPaths", "train_data")
OWNER_DIR = config.get("DataPaths", "owner_data")
RUN_DIR = config.get("DataPaths", "run_data")

# Load dataset

In [8]:
dataset = TrainDataset(config.get("DataPaths", "run_data")).create_dataset()

100%|██████████████████████████████████████████████████████████████████████████████████| 14/14 [00:04<00:00,  2.86it/s]


## Eye movement classification (I-VDT) parameters

In [9]:
curr_model_params = dict(read_json(config.get('EyemovementClassification', 'model_params')))
pprint(curr_model_params)

{'dispersion_threshold': 5,
 'max_saccade_duration_threshold': 0.001,
 'min_fixation_duration_threshold': 0.001,
 'min_saccade_duration_threshold': 0.0002,
 'min_sp_duration_threshold': 0.002,
 'saccade_min_velocity': 4,
 'window_size': 10}


## Parameters search

In [16]:
cls_dataset = classify_eyemovements_wrapper(dataset)

 23%|███████████████████▏                                                               | 3/13 [00:00<00:00, 28.88it/s]

Resulted list of data length: 13


  0%|                                                                                           | 0/13 [00:00<?, ?it/s]


User id: 0
Stimulus type: cat_f#1

User id: 0
Stimulus type: cat_s#1


 15%|████████████▊                                                                      | 2/13 [00:00<00:02,  5.37it/s]

...

 85%|█████████████████████████████████████████████████████████████████████▍            | 11/13 [00:02<00:00,  6.20it/s]

[INFO-FILTER]: found too small sp: [13]!
[INFO-FILTER]: found too small sp: [36]!
[INFO-FILTER]: found too small sp: [432]!
[INFO-FILTER]: found too small sp: [475]!
[INFO-FILTER]: found too small sp: [562]!
[INFO-FILTER]: found too small sp: [936]!
[INFO-FILTER]: found too small sp: [939]!
[INFO-FILTER]: found too small sp: [946]!
[INFO-FILTER]: found too small sp: [949]!

User id: 5
Stimulus type: cat_s#1


 92%|███████████████████████████████████████████████████████████████████████████▋      | 12/13 [00:03<00:00,  3.13it/s]


User id: 5
Stimulus type: cat_s#1


100%|██████████████████████████████████████████████████████████████████████████████████| 13/13 [00:03<00:00,  3.29it/s]


In [17]:
cls_dataset[0].head()

timestamps  stim_X  stim_Y  gaze_X  gaze_Y  frame               timestamp  success  session_id stimulus_type  user_id  x_diff  y_diff  filtered_X  filtered_Y  velocity_X  velocity_Y  velocity_sqrt  stimulus_velocity  acceleration_X  acceleration_sqrt  movements movements_type
0  1.608035e+09     449     121     512     355    884 1970-01-01 00:00:29.433        1           0       cat_f#1        0     -63    -234  415.697402  450.968074   -0.290600   -0.103924       0.308624           1.212452       -0.042009           0.069048          3             sp
1  1.608035e+09     449     121     512     354    884 1970-01-01 00:00:29.433        1           0       cat_f#1        0     -63    -233  415.352939  450.721920   -0.660068   -0.487751       0.820726           1.652504       -0.089816           0.133269          3             sp
2  1.608035e+09     449     121     512     352    885 1970-01-01 00:00:29.467        1           0       cat_f#1        0     -63    -231  414.262473  449.890341   -0.925994   -0.763147       1.199941           2.767721       -0.086648           0.124320          3             sp
3  1.608035e+09     462     123     512     350    885 1970-01-01 00:00:29.467        1           0       cat_f#1        0     -50    -227  412.939250  448.901903   -0.970282   -0.813289       1.266051           3.392102        0.047689           0.070047          3             sp
4  1.608035e+09     462     123     512     348    885 1970-01-01 00:00:29.467        1           0       cat_f#1        0     -50    -225  411.875961  448.151982   -0.746255   -0.597715       0.956117           4.650233        0.239968           0.345118          3             sp

In [18]:
cls_dataset[0].movements_type.value_counts()

sp         768
saccade     56
unknown      4
Name: movements_type, dtype: int64

## Visualization

In [13]:
def visualize_eyemovements(data: pd.DataFrame,
                       x_col: str="x", y_col: str="y",
                       time_col: str='timestamps',
                       color: str="movement_name"):
    assert ((x_col in data.columns) and (y_col in data.columns)
            and (color in data.columns) and (time_col in data.columns))

    color_mapping = dict(read_json(os.path.join(sys.path[0], "settings", "color_mappings.json")))
    data['color'] = data[color].apply(lambda x: color_mapping.get(x, "black"))

    fig = make_subplots(
        rows=2, cols=2,
        shared_xaxes=False,
        vertical_spacing=0.06,
        specs=[[{}, {}],
               [{"colspan": 2}, None]],
        row_heights=[0.4, 0.6],
        subplot_titles=("Gaze X Axis", "Gaze Y Axis", "Gaze X-Y Axis")
    )

    min_ts = np.min(data[time_col])
    for movement_type, df in data.groupby(by=color):
        fig.add_trace(go.Scatter(x=df[time_col] - min_ts,
                                 y=df[x_col],
                                 mode='markers',
                                 marker_color=df['color'],
                                 name=movement_type,
                                 showlegend=False), row=1, col=1)

        fig.add_trace(go.Scatter(x=df[time_col] - min_ts,
                                 y=df[y_col],
                                 mode='markers',
                                 marker_color=df['color'],
                                 name=movement_type,
                                 showlegend=False), row=1, col=2)

        fig.add_trace(go.Scatter(x=df[x_col],
                                 y=df[y_col],
                                 mode='markers',
                                 marker_color=df['color'],
                                 name=movement_type), row=2, col=1)

    fig.update_traces(mode='markers', marker_line_width=0.1, marker_size=4)
    fig.update_layout(height=800, width=1000,
                      title_text="Eyemovements classified")

    fig.update_layout(legend_title_text='Eyemovements Types',
                      legend=dict(font=dict(family="Arial", size=12)))
    fig.update_layout(showlegend=True)
    fig.show()

In [19]:
for i, df in enumerate(cls_dataset):
    print(f"\n\nSession #{i}")
    visualize_eyemovements(df, x_col="gaze_X", y_col="gaze_Y",
                       time_col='timestamps',
                       color='movements_type')



Session #0




Session #1




Session #2




Session #3




Session #4


...



Session #8




Session #9




Session #10




Session #11




Session #12


## Update parameters

In [15]:
update_parameters(fn=config.get('EyemovementClassification', 'model_params'),
                 parameter_name='saccade_min_velocity', new_value=4.5)